In [0]:
!git clone https://github.com/krishnaik06/Stock-Sentiment-Analysis.git

Cloning into 'Stock-Sentiment-Analysis'...
remote: Enumerating objects: 8, done.
remote: Counting objects: 100% (8/8), done.
remote: Compressing objects: 100% (7/7), done.
remote: Total 8 (delta 0), reused 1 (delta 0), pack-reused 0
Unpacking objects: 100% (8/8), done.


In [0]:
### Importing the respective Libraries
import pandas as pd
import numpy as np
import tensorflow as tf
from tensorflow.keras.layers import LSTM, Dense, Bidirectional
from tensorflow.keras.layers import Embedding,Dropout
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot, Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences


print(tf.__version__)

2.2.0


In [0]:
### Read the data
df = pd.read_csv("/content/Stock-Sentiment-Analysis/Data.csv", encoding='latin1')
df.head()

Date  ...                         Top25
0  2000-01-03  ...            Recovering a title
1  2000-01-04  ...  Millennium bug fails to bite
2  2000-01-05  ...                  Useful links
3  2000-01-06  ...   Lessons of law's hard heart
4  2000-01-07  ...                    Gone aloft

[5 rows x 27 columns]

In [0]:
### Now lets check for null values
df.isna().sum()

Date     0
Label    0
Top1     0
Top2     0
Top3     0
Top4     0
Top5     0
Top6     0
Top7     0
Top8     0
Top9     0
Top10    0
Top11    0
Top12    0
Top13    0
Top14    0
Top15    0
Top16    0
Top17    0
Top18    0
Top19    0
Top20    0
Top21    0
Top22    0
Top23    1
Top24    3
Top25    3
dtype: int64

In [0]:
### Fill the null values 
df.fillna("Missing", inplace=True)

In [0]:
### train and test split
train = df[df['Date']<"2015-01-01"]
test = df[df['Date']>"2014-12-31"]

In [0]:
### Do the Feature Engineering
data = train.iloc[:,2:27]

### Replace all the special characters with space
data.replace("[^a-zA-Z]"," ", regex = True, inplace=True)

### Rename the columns names
list1 = [i for i in range(1,26)]
new_index = [str(x) for x in list1]
data.columns = new_index
data.head()

1  ...                            25
0  A  hindrance to operations   extracts from the...  ...            Recovering a title
1                                          Scorecard  ...  Millennium bug fails to bite
2                  Coventry caught on counter by Flo  ...                  Useful links
3                      Pilgrim knows how to progress  ...   Lessons of law s hard heart
4                               Hitches and Horlocks  ...                    Gone aloft

[5 rows x 25 columns]

In [0]:
### Now lower all the words in dataset 
for columns in data.columns:
  data[columns] = data[columns].str.lower()
data.head()

1  ...                            25
0  a  hindrance to operations   extracts from the...  ...            recovering a title
1                                          scorecard  ...  millennium bug fails to bite
2                  coventry caught on counter by flo  ...                  useful links
3                      pilgrim knows how to progress  ...   lessons of law s hard heart
4                               hitches and horlocks  ...                    gone aloft

[5 rows x 25 columns]

In [0]:
### Now form all the data into one array name Headline
headlines = []
for row in range(0, len(data.index)):
  headlines.append(" ".join(str(x) for x in data.iloc[row,0:25]))
headlines

['a  hindrance to operations   extracts from the leaked reports scorecard hughes  instant hit buoys blues jack gets his skates on at ice cold alex chaos as maracana builds up for united depleted leicester prevail as elliott spoils everton s party hungry spurs sense rich pickings gunners so wide of an easy target derby raise a glass to strupar s debut double southgate strikes  leeds pay the penalty hammers hand robson a youthful lesson saints party like it s      wear wolves have turned into lambs stump mike catches testy gough s taunt langer escapes to hit     flintoff injury piles on woe for england hunters threaten jospin with new battle of the somme kohl s successor drawn into scandal the difference between men and women sara denver  nurse turned solicitor diana s landmine crusade put tories in a panic yeltsin s resignation caught opposition flat footed russian roulette sold out recovering a title',
 'scorecard the best lake scene leader  german sleaze inquiry cheerio  boyo the main

In [0]:
### Now do the one hot encoding 
voc_size=5000
onehot_repr = [one_hot(word,voc_size) for word in headlines]
onehot_repr

[[1164,
  2593,
  1498,
  294,
  4776,
  2369,
  2510,
  987,
  4105,
  2598,
  4295,
  2878,
  3065,
  4581,
  3184,
  2060,
  3908,
  2622,
  2385,
  1299,
  2220,
  2045,
  1922,
  3241,
  425,
  160,
  2120,
  1606,
  4575,
  3175,
  4636,
  3332,
  3113,
  2986,
  160,
  2210,
  4583,
  1990,
  2359,
  4593,
  4023,
  3553,
  33,
  3484,
  3055,
  1014,
  4485,
  3573,
  2054,
  2254,
  3610,
  1553,
  3441,
  4481,
  1164,
  1578,
  1498,
  4180,
  2359,
  3612,
  1462,
  4241,
  182,
  376,
  2734,
  2510,
  4899,
  398,
  2493,
  1543,
  1164,
  1797,
  3787,
  481,
  4593,
  3236,
  4508,
  2359,
  2983,
  2401,
  3110,
  4277,
  3487,
  239,
  4796,
  14,
  2966,
  3923,
  4504,
  2359,
  3351,
  390,
  152,
  1498,
  3065,
  2525,
  274,
  4227,
  1299,
  423,
  3175,
  2702,
  1268,
  1135,
  3783,
  1553,
  1682,
  2663,
  2054,
  2510,
  4800,
  3819,
  2359,
  253,
  3205,
  3487,
  2631,
  2510,
  2597,
  791,
  4484,
  377,
  2063,
  4160,
  295,
  3876,
  4277,
  2295

In [0]:
### Pad the words into sequences of 20 words
sent_length = 20
train_sequences = pad_sequences(onehot_repr, maxlen=sent_length, padding='pre')
train_sequences

array([[2493, 1516, 1076, ..., 3581, 1164, 2963],
       [3113, 4920, 2949, ..., 4081, 1498,  767],
       [ 277, 2170, 4914, ...,  264,  558, 4801],
       ...,
       [1925, 3227,  367, ..., 3735, 4380, 3545],
       [2054, 1682,  831, ..., 3680, 1498, 3301],
       [2054, 4262, 3661, ..., 3765, 1212, 2950]], dtype=int32)

In [0]:
### Do the same Procedure for testing data 
data1 = test.iloc[:,2:27]
data1.columns = new_index

data1.replace("[^a-zA-Z]"," ", regex=True, inplace=True)

for columns in data1.columns:
  data1[columns] = data1[columns].str.lower()
data1.head()

1  ...                                                 25
3723  most cases of cancer are the result of sheer b...  ...  authorities pull plug on russia s last politic...
3724  moscow  gt beijing high speed train will reduc...  ...                      china scraps rare earths caps
3725                    us oil falls below     a barrel  ...  tests over  india set to make the iris of bigg...
3726                 shots fired  at french magazine hq  ...   ebola vaccine trials in halifax so far a success
3727  new charlie hebdo issue to come out next week ...  ...  young mother let terrorists into charlie hebdo...

[5 rows x 25 columns]

In [0]:
test_transform=[]
for row in range(0, len(data1.index)):
  test_transform.append(" ".join(str(x) for x in data1.iloc[row,0:25]))
test_transform[0]

'most cases of cancer are the result of sheer bad luck rather than unhealthy lifestyles  diet or even inherited genes  new research suggests  random mutations that occur in dna when cells divide are responsible for two thirds of adult cancers across a wide range of tissues  iran dismissed united states efforts to fight islamic state as a ploy to advance u s  policies in the region   the reality is that the united states is not acting to eliminate daesh  they are not even interested in weakening daesh  they are only interested in managing it  poll  one in   germans would join anti muslim marches uk royal family s prince andrew named in us lawsuit over underage sex allegations some    asylum seekers refused to leave the bus when they arrived at their destination in rural northern sweden  demanding that they be taken back to malm or  some big city   pakistani boat blows self up after india navy chase  all four people on board the vessel from near the pakistani port city of karachi are bel

In [0]:
onehot_test = [one_hot(words,voc_size) for words in test_transform]
test_sequences = pad_sequences(onehot_test, maxlen=sent_length, padding='pre')
test_sequences

array([[1682, 4980, 2274, ..., 1622, 3922,  114],
       [ 354, 4320, 1925, ..., 2579, 2413,  738],
       [1228, 4053, 3889, ...,  281, 3788, 2080],
       ...,
       [  90, 3138, 2185, ..., 1498, 4277, 2798],
       [2220, 1225, 2931, ..., 1097, 2369, 4767],
       [4727, 1850, 4661, ..., 3110, 1164, 1859]], dtype=int32)

In [0]:
### Build the Model
embedding_size=40

### Initiating the Model
model =Sequential()

### Adding the embedding layer
model.add(Embedding(input_dim=voc_size,
                    output_dim=embedding_size,
                    input_length=sent_length))
### Intiate The bidirectional LSTM and adding dropout layers
model.add(Bidirectional(LSTM(units=100, activation='relu')))
model.add(Dropout(0.5))

### Make the Model into Fully Connected Layer
model.add(Dense(1, activation='sigmoid'))

In [0]:
### Set the Optimizer and other terms for model
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['accuracy'])

In [0]:
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, 20, 40)            200000    
_________________________________________________________________
bidirectional (Bidirectional (None, 200)               112800    
_________________________________________________________________
dropout (Dropout)            (None, 200)               0         
_________________________________________________________________
dense (Dense)                (None, 1)                 201       
Total params: 313,001
Trainable params: 313,001
Non-trainable params: 0
_________________________________________________________________


In [0]:
train_label = train['Label']
train_label.head()

0    0
1    0
2    0
3    1
4    1
Name: Label, dtype: int64

In [0]:
test_label = test['Label']
test_label.head()

3723    1
3724    0
3725    0
3726    1
3727    1
Name: Label, dtype: int64

In [0]:
### Transform the elements into array
x_final = np.array(train_sequences)
y_final = np.array(test_sequences)

x_label = np.array(train_label)
y_label = np.array(test_label)

In [0]:
### Finally Training
model.fit(x_final, x_label,batch_size=64,epochs=10,validation_data=(y_final,y_label))

Epoch 1/10
59/59 [==============================] - 6s 107ms/step - loss: 0.6922 - accuracy: 0.5291 - val_loss: 0.6936 - val_accuracy: 0.5079
Epoch 2/10
59/59 [==============================] - 6s 98ms/step - loss: 0.6870 - accuracy: 0.5308 - val_loss: 0.6978 - val_accuracy: 0.5079
Epoch 3/10
59/59 [==============================] - 6s 102ms/step - loss: 0.7073 - accuracy: 0.5944 - val_loss: 0.6938 - val_accuracy: 0.5026
Epoch 4/10
59/59 [==============================] - 6s 100ms/step - loss: 0.5681 - accuracy: 0.7768 - val_loss: 0.8778 - val_accuracy: 0.5450
Epoch 5/10
59/59 [==============================] - 6s 108ms/step - loss: 0.4044 - accuracy: 0.8439 - val_loss: 1.5753 - val_accuracy: 0.5661
Epoch 6/10
59/59 [==============================] - 6s 105ms/step - loss: 0.3358 - accuracy: 0.9065 - val_loss: 2.4667 - val_accuracy: 0.5556
Epoch 7/10
59/59 [==============================] - 6s 101ms/step - loss: 0.4657 - accuracy: 0.9116 - val_loss: 3.6467 - val_accuracy: 0.5556
Epoch 8

In [0]:
### Save the Model
model.save("BidirectionalLSTM.h5")